# GPM Domain Cumulative Distribution Functions

In [1]:
import numpy as np
import pygrib
import netCDF4
import xarray
import pyproj
import pandas as pd
from datetime import datetime, timedelta

In [2]:
path0 = '/uufs/chpc.utah.edu/common/home/horel-group4/tmccorkle/imerg_early/'
gpm0 = '2018_daily/3B-DAY-E.MS.MRG.3IMERG.20180601-S000000-E235959.V05.nc4.nc'
ncfile = netCDF4.Dataset(path0+gpm0, 'r')
nclat = ncfile.variables['lat']
nclon = ncfile.variables['lon']
nclat = np.array(nclat)
nclon = np.array(nclon)
#ncfile.close()


a = len(nclat)
b = len(nclon)
lon2 = np.zeros((b,a))
lat2 = np.zeros((b,a))

lat2[0:b,:] = nclat

for n in range(0,a):
    lon2[:,n] = nclon
    
lat = lat2[90:475,1400:1610]
lon = lon2[90:475,1400:1610]

In [3]:
dates = []

# Time increment function
def perdelta(start, end, delta):
    current = start
    while current < end:
        yield current
        current +=delta

# Set up hourly time stamps
start = datetime(2018, 6, 1, 0, 0)
end = datetime(2018, 9, 1, 0, 0)

for times in perdelta(start, end, timedelta(1)):
    dates.append(datetime.strftime(times, '%m%d'))

In [4]:
path = '/uufs/chpc.utah.edu/common/home/u1014509/ak_fire/precip/nws/'
file = '2014_2018_nws_daily.csv'
met = 'metadata_nws.csv'

raws = pd.read_csv(path+file,header=None)
#daily_raws = raws.values
#stn_prec_hist = raws.mask(raws < -1000)
daily_raws = raws.values

meta = pd.read_csv(path+met,header=None)
raws_meta = meta.values

In [7]:
# Create the arrays
# GPM (385,210)

#daily_raws = daily_stn.mask(daily_stn.isna(), -9999)
#np.savetxt(path+'2014_2018_nws_daily.csv',daily_raws,delimiter=',')
#daily_raws = daily_raws.values

n = 155
cdf_99 = np.zeros((n))
cdf_95 = np.zeros((n))
cdf_90 = np.zeros((n))
cdf_85 = np.zeros((n))
cdf_80 = np.zeros((n))
cdf_75 = np.zeros((n))
cdf_70 = np.zeros((n))
cdf_65 = np.zeros((n))
cdf_60 = np.zeros((n))



perc_10mm = np.zeros((n))
perc_5mm = np.zeros((n))
perc_2mm = np.zeros((n))
perc_1mm = np.zeros((n))

### Calculate Station CDFs

In [8]:
for i in range(0,n):
    if ((daily_raws[:,i] < 0).sum()) < 46:
        
        l = np.arange(0,np.max(daily_raws[:,i]),0.25)

        if len(l) < 2:
            pass

        else:
            bins = l

            counts, bin_edges = np.histogram(daily_raws[:,i],range=[0,np.max(daily_raws[:,i])],bins=bins)
            cdf = np.cumsum(counts)
            cdf_1 = cdf/cdf[-1]

            idx0 = np.abs(cdf_1-0.99).argmin()
            idx = np.abs(cdf_1-0.95).argmin()
            idx1 = np.abs(cdf_1-0.90).argmin()
            idx2 = np.abs(cdf_1-0.85).argmin()
            idx3 = np.abs(cdf_1-0.80).argmin()
            idx4 = np.abs(cdf_1-0.75).argmin()
            idx5 = np.abs(cdf_1-0.70).argmin()
            idx6 = np.abs(cdf_1-0.65).argmin()
            idx7 = np.abs(cdf_1-0.60).argmin()

            cdf_99[i] = bin_edges[idx0+1]
            cdf_95[i] = bin_edges[idx+1]
            cdf_90[i] = bin_edges[idx1+1]
            cdf_85[i] = bin_edges[idx2+1]
            cdf_80[i] = bin_edges[idx3+1]
            cdf_75[i] = bin_edges[idx4+1]
            cdf_70[i] = bin_edges[idx5+1]
            cdf_65[i] = bin_edges[idx6+1]
            cdf_60[i] = bin_edges[idx7+1]
                
                
                        
            #idx_p = np.abs(bin_edges-1).argmin()
            #perc_1mm[i] = cdf_1[idx_p-1]
            
            #idx_p2 = np.abs(bin_edges-2.5).argmin()
            #perc_2mm[i] = cdf_1[idx_p2-1]
            
            #idx_p3 = np.abs(bin_edges-5).argmin()
            #perc_5mm[i] = cdf_1[idx_p3-1]
            
            #idx_p4 = np.abs(bin_edges-10).argmin()
            #perc_10mm[i] = cdf_1[idx_p4-1]
            
            


    else:
        cdf_99[i] = np.nan
        cdf_95[i] = np.nan
        cdf_90[i] = np.nan
        cdf_85[i] = np.nan
        cdf_80[i] = np.nan
        cdf_75[i] = np.nan
        cdf_70[i] = np.nan
        cdf_65[i] = np.nan
        cdf_60[i] = np.nan

        #cdf_low[i] = np.nan

        #max_mm[i] = np.nan


### Calculate GPM CDFs

In [ ]:
loc = '/uufs/chpc.utah.edu/common/home/horel-group4/tmccorkle/imerg_early/'

pre = ['2014_daily/3B-DAY-E.MS.MRG.3IMERG.2014',
      '2015_daily/3B-DAY-E.MS.MRG.3IMERG.2015',
      '2016_daily/3B-DAY-E.MS.MRG.3IMERG.2016',
      '2017_daily/3B-DAY-E.MS.MRG.3IMERG.2017',
      '2018_daily/3B-DAY-E.MS.MRG.3IMERG.2018']


# GPM Grid Points over AK [90:475,1400:1610]
for r in range(90,475):

    imerg_prec = np.zeros((460,210))
    rr = r-90

    for p in range(0,5):
        yr = loc+pre[p]
        if (p==0):
            n = 2
        else:
            n = 0

        for d in range(n,92):
            row = (92*p)+d
            #row = d

            day = dates[d]
            dayfile = day+'-S000000-E235959.V05.nc4.nc'

            ncfile = netCDF4.Dataset(yr+dayfile, 'r')
            ncprec = ncfile.variables['HQprecipitation'][r,1400:1610]
            #ncgood = ncfile.variables['precipitationCal_cnt'][r,1400:1610]
            ncfile.close
            

            imerg_prec[row,:] = ncprec

    for i in range(0,210):

        if ((imerg_prec[:,i] < 0).sum()) < 46:
        
            l = np.arange(0,np.max(imerg_prec[:,i]),0.25)

            if len(l) < 2:
                pass

            else:
                bins = l

                counts, bin_edges = np.histogram(imerg_prec[:,i],range=[0,np.max(imerg_prec[:,i])],bins=bins)
                cdf = np.cumsum(counts)
                cdf_1 = cdf/cdf[-1]

                idx0 = np.abs(cdf_1-0.99).argmin()
                idx = np.abs(cdf_1-0.95).argmin()
                idx1 = np.abs(cdf_1-0.90).argmin()
                idx2 = np.abs(cdf_1-0.85).argmin()
                idx3 = np.abs(cdf_1-0.80).argmin()
                idx4 = np.abs(cdf_1-0.75).argmin()
                idx5 = np.abs(cdf_1-0.70).argmin()
                idx6 = np.abs(cdf_1-0.65).argmin()
                idx7 = np.abs(cdf_1-0.60).argmin()

                cdf_99[rr,i] = bin_edges[idx0+1]
                cdf_95[rr,i] = bin_edges[idx+1]
                cdf_90[rr,i] = bin_edges[idx1+1]
                cdf_85[rr,i] = bin_edges[idx2+1]
                cdf_80[rr,i] = bin_edges[idx3+1]
                cdf_75[rr,i] = bin_edges[idx4+1]
                cdf_70[rr,i] = bin_edges[idx5+1]
                cdf_65[rr,i] = bin_edges[idx6+1]
                cdf_60[rr,i] = bin_edges[idx7+1]

            
            
            
            #idx2 = np.abs(bin_edges-1).argmin()
            #perc_10mm[rr,i] = cdf_1[idx2-1]

            

            #try:
                #cdf_low[rr,i] = cdf_1[1]

                #max_mm[rr,i] = bin_edges[-1]

            #except:
                #pass


    else:
        cdf_99[rr,i] = np.nan
        cdf_95[rr,i] = np.nan
        cdf_90[rr,i] = np.nan
        cdf_85[rr,i] = np.nan
        cdf_80[rr,i] = np.nan
        cdf_75[rr,i] = np.nan
        cdf_70[rr,i] = np.nan
        cdf_65[rr,i] = np.nan
        cdf_60[rr,i] = np.nan

        #cdf_low[rr,i] = np.nan

        #max_mm[rr,i] = np.nan


In [ ]:
perc_1mm[perc_1mm == 0] = np.nan
perc_2mm[perc_2mm == 0] = np.nan
perc_5mm[perc_5mm == 0] = np.nan
perc_10mm[perc_10mm == 0] = np.nan

### Create Percentile NetCDF4 File

In [12]:
ncfile = 'nws_cdf_2014_2018.nc'
dataset = netCDF4.Dataset(path+ncfile,'w',format='NETCDF4_CLASSIC')

xdim = dataset.createDimension('xdim',155)
#ydim = dataset.createDimension('ydim', 210)


latitudes = dataset.createVariable('latitude', np.float32,('xdim'))
longitudes = dataset.createVariable('longitude', np.float32,('xdim'))
cdf99 = dataset.createVariable('Percentile99', np.float32,('xdim'))
cdf95 = dataset.createVariable('Percentile95', np.float32,('xdim'))
cdf90 = dataset.createVariable('Percentile90', np.float32,('xdim'))
cdf85 = dataset.createVariable('Percentile85', np.float32,('xdim'))
cdf80 = dataset.createVariable('Percentile80', np.float32,('xdim'))
cdf75 = dataset.createVariable('Percentile75', np.float32,('xdim'))
cdf70 = dataset.createVariable('Percentile70', np.float32,('xdim'))
cdf65 = dataset.createVariable('Percentile65', np.float32,('xdim'))
cdf60 = dataset.createVariable('Percentile60', np.float32,('xdim'))


latitudes[:] = raws_meta[0,:]
longitudes[:] = raws_meta[1,:]

cdf99[:] = cdf_99
cdf95[:] = cdf_95
cdf90[:] = cdf_90
cdf85[:] = cdf_85
cdf80[:] = cdf_80
cdf75[:] = cdf_75
cdf70[:] = cdf_70
cdf65[:] = cdf_65
cdf60[:] = cdf_60


dataset = netCDF4.Dataset(path+ncfile,'a',format='NETCDF4_CLASSIC')

latitudes[:] = raws_meta[0,:]
longitudes[:] = raws_meta[1,:]

cdf99[:] = cdf_99
cdf95[:] = cdf_95
cdf90[:] = cdf_90
cdf85[:] = cdf_85
cdf80[:] = cdf_80
cdf75[:] = cdf_75
cdf70[:] = cdf_70
cdf65[:] = cdf_65
cdf60[:] = cdf_60
            
dataset.close()


In [ ]:
ncfile = 'imerge_cdf_2014_2018.nc'
dataset = netCDF4.Dataset(loc+ncfile,'w',format='NETCDF4_CLASSIC')

xdim = dataset.createDimension('xdim', 385)
ydim = dataset.createDimension('ydim', 210)


latitudes = dataset.createVariable('latitude', np.float32,('xdim','ydim'))
longitudes = dataset.createVariable('longitude', np.float32,('xdim','ydim'))
cdf99 = dataset.createVariable('Percentile99', np.float32,('xdim','ydim'))
cdf95 = dataset.createVariable('Percentile95', np.float32,('xdim','ydim'))
cdf90 = dataset.createVariable('Percentile90', np.float32,('xdim','ydim'))
cdf85 = dataset.createVariable('Percentile85', np.float32,('xdim','ydim'))
cdf80 = dataset.createVariable('Percentile80', np.float32,('xdim','ydim'))
cdf75 = dataset.createVariable('Percentile75', np.float32,('xdim','ydim'))
cdf70 = dataset.createVariable('Percentile70', np.float32,('xdim','ydim'))
cdf65 = dataset.createVariable('Percentile65', np.float32,('xdim','ydim'))
cdf60 = dataset.createVariable('Percentile60', np.float32,('xdim','ydim'))


latitudes[:] = lat
longitudes[:] = lon

cdf99[:] = cdf_99
cdf95[:] = cdf_95
cdf90[:] = cdf_90
cdf85[:] = cdf_85
cdf80[:] = cdf_80
cdf75[:] = cdf_75
cdf70[:] = cdf_70
cdf65[:] = cdf_65
cdf60[:] = cdf_60


dataset = netCDF4.Dataset(loc+ncfile,'a',format='NETCDF4_CLASSIC')

latitudes[:] = lat
longitudes[:] = lon

cdf99[:] = cdf_99
cdf95[:] = cdf_95
cdf90[:] = cdf_90
cdf85[:] = cdf_85
cdf80[:] = cdf_80
cdf75[:] = cdf_75
cdf70[:] = cdf_70
cdf65[:] = cdf_65
cdf60[:] = cdf_60
            
dataset.close()

In [ ]:
c95 = pd.read_csv(path+'cdf_95_nws.csv',header=None)
raws_95 = c95.values

c75 = pd.read_csv(path+'cdf_75_nws.csv',header=None)
raws_75 = c75.values

raw1 = pd.read_csv(path+'nws_percentile_1mm.csv',header=None)
raws_1mm = raw1.values

raw2 = pd.read_csv(path+'nws_percentile_2mm.csv',header=None)
raws_2mm = raw2.values

raw5 = pd.read_csv(path+'nws_percentile_5mm.csv',header=None)
raws_5mm = raw5.values

raw10 = pd.read_csv(path+'nws_percentile_10mm.csv',header=None)
raws_10mm = raw10.values

### Read in information

In [ ]:
loc = '/uufs/chpc.utah.edu/common/home/horel-group4/tmccorkle/imerg_early/'
cdf95 = pd.read_csv(loc+'cdf_95.csv',header=None)
gpm_cdf95 = cdf95.values

cdf75 = pd.read_csv(loc+'cdf_75.csv',header=None)
gpm_cdf75 = cdf75.values

cdflow = pd.read_csv(loc+'cdf_low.csv',header=None)
gpm_cdflow = cdflow.values

cdfmax = pd.read_csv(loc+'cdf_max.csv',header=None)
gpm_cdfmax = cdfmax.values

i_2 = pd.read_csv(loc+'gpm_percentile_2.5mm_pmw.csv',header=None)
gpm_2mm = i_2.values

i_1 = pd.read_csv(loc+'gpm_percentile_1mm_pmw.csv',header=None)
gpm_1mm = i_1.values

i_5 = pd.read_csv(loc+'gpm_percentile_5mm_pmw.csv',header=None)
gpm_5mm = i_5.values

i_10 = pd.read_csv(loc+'gpm_percentile_10mm_pmw.csv',header=None)
gpm_10mm = i_10.values

In [ ]:
loc2 = '/uufs/chpc.utah.edu/common/home/horel-group4/tmccorkle/rfc_precip/'
r_cdf95 = pd.read_csv(loc2+'rfc_cdf_95.csv',header=None)
rfc_cdf95 = r_cdf95.values

r_cdf75 = pd.read_csv(loc2+'rfc_cdf_75.csv',header=None)
rfc_cdf75 = r_cdf75.values

r_cdflow = pd.read_csv(loc2+'rfc_cdf_low.csv',header=None)
rfc_cdflow = r_cdflow.values

r_cdfmax = pd.read_csv(loc2+'rfc_cdf_max.csv',header=None)
rfc_cdfmax = r_cdfmax.values

r_2 = pd.read_csv(loc2+'rfc_percentile_2.5mm.csv',header=None)
rfc_2mm = r_2.values

r_1 = pd.read_csv(loc2+'rfc_percentile_1mm.csv',header=None)
rfc_1mm = r_1.values

r_5 = pd.read_csv(loc2+'rfc_percentile_5mm.csv',header=None)
rfc_5mm = r_5.values

r_10 = pd.read_csv(loc2+'rfc_percentile_10mm.csv',header=None)
rfc_10mm = r_10.values

### Downscale to RFC Grid

In [ ]:
grbs = pygrib.open('/uufs/chpc.utah.edu/common/home/horel-group4/tmccorkle/rfc_precip/2018/precip_acr_grid_00_06_20180601.grb')
for grb in grbs:
    grb

rfclat, rfclon = grb.latlons()

In [ ]:
from scipy import spatial

lat_lon = np.dstack([raws_meta[0,:].ravel(),raws_meta[1,:].ravel()])[0]
#lat_lon = np.dstack([lat.ravel(),lon.ravel()])[0]
rfc_lat_lon = np.dstack([rfclat.ravel(),rfclon.ravel()])[0]
#gpm_lat_lon = np.dstack([lat.ravel(),lon.ravel()])[0]



distance,index2 = spatial.KDTree(rfc_lat_lon).query(lat_lon)

In [ ]:
gpm_1mm_flat = np.ndarray.flatten(gpm_1mm)
gpm_2mm_flat = np.ndarray.flatten(gpm_2mm)
gpm_5mm_flat = np.ndarray.flatten(gpm_5mm)
gpm_10mm_flat = np.ndarray.flatten(gpm_10mm)

In [ ]:
rfc_1mm_flat = np.ndarray.flatten(rfc_1mm)
rfc_2mm_flat = np.ndarray.flatten(rfc_2mm)
rfc_5mm_flat = np.ndarray.flatten(rfc_5mm)
rfc_10mm_flat = np.ndarray.flatten(rfc_10mm)

In [ ]:
#gpm1_to_rfc = np.zeros((243800))
#gpm2_to_rfc = np.zeros((243800))
#gpm5_to_rfc = np.zeros((243800))
#gpm10_to_rfc = np.zeros((243800))

raws1_to_rfc = np.zeros((len(index2)))
raws2_to_rfc = np.zeros((len(index2)))
raws5_to_rfc = np.zeros((len(index2)))
raws10_to_rfc = np.zeros((len(index2)))


for i in range(0,len(index2)):
    idx = index2[i]
    #gpm1_to_rfc[i] = gpm_1mm_flat[idx]
    #gpm2_to_rfc[i] = gpm_2mm_flat[idx]
    #gpm5_to_rfc[i] = gpm_5mm_flat[idx]
    #gpm10_to_rfc[i] = gpm_10mm_flat[idx]
    
    raws1_to_rfc[i] = rfc_1mm_flat[idx]
    raws2_to_rfc[i] = rfc_2mm_flat[idx]
    raws5_to_rfc[i] = rfc_5mm_flat[idx]
    raws10_to_rfc[i] = rfc_10mm_flat[idx]
    
#gpm1_rfc = np.reshape(gpm1_to_rfc, (530,460))
#gpm2_rfc = np.reshape(gpm2_to_rfc, (530,460))
#gpm5_rfc = np.reshape(gpm5_to_rfc, (530,460))
#gpm10_rfc = np.reshape(gpm10_to_rfc, (530,460))

In [ ]:
#diff1mm = gpm1_rfc - rfc_1mm
#diff2mm = gpm2_rfc - rfc_2mm
#diff5mm = gpm5_rfc - rfc_5mm
#diff10mm = gpm10_rfc - rfc_10mm
 
rfc_diff1mm = raws1_to_rfc - perc_1mm
rfc_diff2mm = raws2_to_rfc - perc_2mm
rfc_diff5mm = raws5_to_rfc - perc_5mm
rfc_diff10mm = raws10_to_rfc - perc_10mm

gpm_diff1mm = raws1_to_gpm - perc_1mm
gpm_diff2mm = raws2_to_gpm - perc_2mm
gpm_diff5mm = raws5_to_gpm - perc_5mm
gpm_diff10mm = raws10_to_gpm - perc_10mm

# Plot the data

In [ ]:
from mpl_toolkits.basemap import Basemap
import matplotlib.pyplot as plt
import matplotlib as mpl

In [ ]:
figloc = '/uufs/chpc.utah.edu/common/home/u1014509/public_html/phd/imerg_e/cdf/'
fig = plt.figure(figsize = (10,10))
ax = fig.add_subplot(111)

levels = np.arange(-.2,.21,.05)
plt.title('IMERG-NWS 10mm 24-Hr Precip Percentile Difference', fontsize=18)
cmap=plt.cm.RdYlBu

bmap = Basemap(resolution='i',projection='merc',llcrnrlat=55,urcrnrlat=71,llcrnrlon=-171,urcrnrlon=-132.5)

bmap.drawcoastlines(linewidth=1.5)
bmap.drawcountries(linewidth=1.5)
bmap.drawstates(linewidth=1.5)

stnx,stny = bmap(raws_meta[1,:],raws_meta[0,:])
x,y = bmap(rfclon,rfclat)

#cs = bmap.contourf(x,y,diff10mm,levels=levels,cmap=cmap,alpha=0.85)
cs = bmap.scatter(stnx,stny,c=gpm_diff10mm,s=130,cmap=cmap,norm=mpl.colors.BoundaryNorm(levels,cmap.N),edgecolor='k',zorder=99)
cb_ax = fig.add_axes([.16,.06,.7,.4],visible=None)
cbar = plt.colorbar(cs,ax=cb_ax,ticks=[-.5,-.4,-.3,-.2,-.1,0,.1,.2,.3,.4,.5],orientation='horizontal')
cbar.ax.set_xticklabels(['-.5','-.4','-.3','-.2','-.1','0','.1','.2','.3','.4','.5'], fontsize=13.5)
cbar.ax.set_xlabel('Percentile', fontsize=15)

fig.savefig(figloc+'gpm_nws_diff_10mm_perc.png', bbox_inches='tight')

In [ ]:
fig = plt.figure(figsize = (10,10))
ax = fig.add_subplot(111)

levels2 = np.arange(.4,1.01,.025)
levels = np.arange(0,7,.5)
levels3 = np.arange(-25,26,5)

cmap = plt.cm.jet

#plt.title('IMERG 75th percentile Daily Precip (PMW Only)\nJune-August 2014-2018', fontsize=18)
#plt.title('IMERG 95th percentile Daily Precip Diff (All-PMW)\nJune-August 2014-2018', fontsize=18)
#plt.title('IMERG Smallest Bin Percentile (PMW Only)\nDaily Precip June-August 2014-2018', fontsize=18)
plt.title('IMERG and NWS 10mm Daily Precip Percentile\nJune-August 2014-2018', fontsize=18)
bmap = Basemap(resolution='i',projection='merc',llcrnrlat=55,urcrnrlat=71,llcrnrlon=-171,urcrnrlon=-132.5)

bmap.drawcoastlines(linewidth=1.5)
bmap.drawcountries(linewidth=1.5)
bmap.drawstates(linewidth=1.5)

x,y = bmap(lon,lat)
rfcx,rfcy = bmap(rfclon,rfclat)
stnx,stny = bmap(raws_meta[1,:],raws_meta[0,:])

cs = bmap.contourf(x,y,gpm_10mm,levels=levels2,cmap=cmap,extend='min')
bmap.scatter(stnx,stny,c=perc_10mm,s=130,cmap=cmap,norm=mpl.colors.BoundaryNorm(levels2,cmap.N),edgecolor='k',zorder=99)

cb_ax = fig.add_axes([.16,.06,.7,.4],visible=None)
cbar = plt.colorbar(cs,ax=cb_ax,ticks=[.4,.5,.6,.7,.8,.9,1],orientation='horizontal')
cbar.ax.set_xticklabels(['.4','.5','.6','.7','.8','.9','1'], fontsize=13.5)
cbar.ax.set_xlabel('Percentile', fontsize=15)
fig.savefig('/uufs/chpc.utah.edu/common/home/u1014509/public_html/phd/imerg_e/cdf/gpm_nws_10mm_perc.png', bbox_inches='tight')
#ticks=[0,.1,.2,.3,.4,.5,.6,.7,.8,.9,1]   ['0','.1','.2','.3','.4','.5','.6','.7','.8','.9','1']

'''

cs = bmap.contourf(x,y,diff,levels=levels3,cmap=plt.cm.BrBG,extend='both')
cb_ax = fig.add_axes([.16,.06,.7,.4],visible=None)
cbar = plt.colorbar(cs,ax=cb_ax,ticks=[-25,-20,-15,-10,-5,0,5,10,15,20,25],orientation='horizontal')
cbar.ax.set_xticklabels(['-25','-20','-15','-10','-5','0','5','10','15','20','25'], fontsize=13.5)
cbar.ax.set_xlabel('Precipitation (mm)', fontsize=15)
fig.savefig('/uufs/chpc.utah.edu/common/home/u1014509/public_html/phd/imerg_e/diff_95_pmw.png', bbox_inches='tight')




cs = bmap.contourf(x,y,cdf_75,levels=levels,cmap=plt.cm.jet,extend='max')
cb_ax = fig.add_axes([.16,.06,.7,.4],visible=None)
cbar = plt.colorbar(cs,ax=cb_ax,ticks=[0,1,2,3,4,5,6,7],orientation='horizontal') #,8,9,10],
cbar.ax.set_xticklabels(['0','1','2','3','4','5','6','7'], fontsize=13.5) #,'8','9','10'], fontsize=13.5)
cbar.ax.set_xlabel('Precipitation (mm)', fontsize=15)
fig.savefig('/uufs/chpc.utah.edu/common/home/u1014509/public_html/phd/imerg_e/gpm_75_pmw.png', bbox_inches='tight')

'''